In [ ]:
# %%bash

# mamba install scanpy=1.8.2 anndata=0.7.8 umap-learn=0.5.2 numpy=1.20.1 scipy=1.6.2 pandas=1.4.1 scikit-learn=0.24.1 statsmodels=0.12.2 python-igraph=0.9.8 pynndescent=0.5.5

In [1]:
import genomepy
import numpy as np
import pandas as pd
import scanpy as sc
from collections import Counter
import math

In [2]:
sc.settings.verbosity = 3
sc.logging.print_header()
sc.settings.set_figure_params(dpi=80, facecolor='white')

scanpy==1.8.2 anndata==0.7.8 umap==0.5.2 numpy==1.20.1 scipy==1.6.2 pandas==1.4.1 scikit-learn==0.24.1 statsmodels==0.12.2 python-igraph==0.9.8 pynndescent==0.5.5


In [3]:
def counts2tpm(df):
    """
    convert read counts to TPM (transcripts per million)
    """
    gene_names = df.index
    sample_names = [c for c in df.columns if c != "length"]

    sample_reads = df.loc[:, sample_names].copy()
    gene_len = df.loc[:, ['length']]
    rate = sample_reads.values / gene_len.values
    tpm = rate / np.sum(rate, axis=0).reshape(1, -1) * 1e6
    return pd.DataFrame(data=tpm, columns=sample_names, index=gene_names)

a = pd.DataFrame(data = {
    'Gene': ("A","B","C","D","E"),
    'length': (100, 50, 25, 5, 1),
     'S1': (80, 10,  6,  3,   1),
     'S2': (20, 20, 10, 50, 400)
}).set_index("Gene")

tpms = counts2tpm(a)
print(tpms.head(2))

                 S1          S2
Gene                           
A     281690.140845  486.618005
B      70422.535211  973.236010


In [4]:
a = genomepy.Annotation("/bank/genomes/Smed")
lengths = a.lengths()

# genes to remove
blacklist = [
    "MT-1",  # the whole mitochondrion?
]

# convert the raw counts to counts/tpms per cluster

In [ ]:
# counts = pd.read_csv("./raw/raw_counts.csv", index_col=0, dtype=int).transpose()
# counts = counts[~counts.index.isin(blacklist)]
# counts.head(3)

In [ ]:
# tpms = counts2tpm(counts.join(lengths))
# tpms.head(3)

In [ ]:
# counts.to_csv("counts_per_cluster.tsv", sep="\t")
# tpms.to_csv("tpms_per_cluster.tsv", sep="\t")

# load raw counts per cell

In [34]:
adata_u = sc.read_10x_mtx(
    "raw/Final_counts_10xformat/",
    var_names='gene_symbols',
    cache=True)

... reading from cache file cache/raw-Final_counts_10xformat-matrix.h5ad


In [35]:
adata_u.X

<103654x26966 sparse matrix of type '<class 'numpy.float32'>'
	with 25995385 stored elements in Compressed Sparse Row format>

In [36]:
counts = pd.DataFrame.sparse.from_spmatrix(adata_u.X.T, index=adata_u.var_names, columns=adata_u.obs.index)
counts = counts[~counts.index.isin(blacklist)]
counts.head(5)

L1_CACTTCGACAGCGTTAGCGAGTAA  L1_AGAGTCAAAGCCATGCGACTAGTA  \
SMEST000017001                          0.0                          0.0   
SMEST000022001                          0.0                          0.0   
SMEST000026001                          0.0                          0.0   
SMEST000041001                          0.0                          0.0   
SMEST000044001                          0.0                          0.0   

                L1_ACAAGCTATGGCTTCAAGATGTAC  L1_AACGCTTAGTCGTAGAAGATCGCA  \
SMEST000017001                          0.0                          0.0   
SMEST000022001                          0.0                          0.0   
SMEST000026001                          0.0                          0.0   
SMEST000041001                          0.0                          0.0   
SMEST000044001                          0.0                          0.0   

                L1_ATCCTGTAGAATCTGATCCGTCTA  L1_ATTGAGGAACAGCAGAATTGAGGA  \
SMEST000017001                          0.0                          0.0   
SMEST000022001                          0.0                          0.0   
SMEST000026001                          0.0                          0.0   
SMEST000041001                          0.0                          0.0   
SMEST000044001                          0.0                          0.0   

                L1_CATCAAGTTGGCTTCACACTTCGA  L1_AAGGTACACCGACAACAGAGTCAA  \
SMEST000017001                          0.0                          0.0   
SMEST000022001                          0.0                          0.0   
SMEST000026001                          0.0                          0.0   
SMEST000041001                          0.0                          0.0   
SMEST000044001                          0.0                          0.0   

                L1_GAATCTGAATGCCTAAATCATTCC  L1_CCGTGAGAGAACAGGCCTGGCATA  ...  \
SMEST000017001                          0.0                          0.0  ...   
SMEST000022001                          0.0                          0.0  ...   
SMEST000026001                          0.0                          0.0  ...   
SMEST000041001                          0.0                          0.0  ...   
SMEST000044001                          0.0                          0.0  ...   

                L25_ACCTCCAACTAAGGTCTATCAGCA  L25_ACGTATCATGGTGGTAGATGAATC  \
SMEST000017001                           0.0                           0.0   
SMEST000022001                           0.0                           0.0   
SMEST000026001                           0.0                           0.0   
SMEST000041001                           0.0                           0.0   
SMEST000044001                           0.0                           0.0   

                L25_ACCTCCAAACATTGGCACTATGCA  L25_ACAGCAGAGTCTGTCAAGAGTCAA  \
SMEST000017001                           0.0                           0.0   
SMEST000022001                           0.0                           0.0   
SMEST000026001                           0.0                           0.0   
SMEST000041001                           0.0                           0.0   
SMEST000044001                           0.0                           0.0   

                L25_ACAGCAGAAACCGAGAAGTGGTCA  L25_ACGCTCGACGACACACCAAGGAGC  \
SMEST000017001                           0.0                           0.0   
SMEST000022001                           0.0                           0.0   
SMEST000026001                           0.0                           0.0   
SMEST000041001                           0.0                           0.0   
SMEST000044001                           0.0                           0.0   

                L25_AGAGTCAAGAGTTAGCCCGAAGTA  L25_ACGTATCAACACAGAAAGGCTAAC  \
SMEST000017001                           0.0                           0.0   
SMEST000022001                           0.0                           0.0   
SMEST000026001                           0.0                

# save raw counts per cell (huge & slow)

In [ ]:
# dense = counts.sparse.to_dense()

In [ ]:
# dense = dense.astype(int)

In [ ]:
# dense

In [ ]:
# dense.head(5).sum(1)

In [ ]:
# dense.to_csv('counts_per_cell.tsv.gz', sep="\t")

In [ ]:
# dense.to_csv('counts_per_cell.tsv', sep="\t")  # waaaaay to big to load into DESeq2

# clusters per cell

In [25]:
adata_p = sc.read_h5ad('raw/Final_counts.h5ad')

/home/siebrenf/miniconda3/envs/grn/lib/python3.9/site-packages/anndata/compat/__init__.py:180: FutureWarning: Moving element from .uns['neighbors']['distances'] to .obsp['distances'].

This is where adjacency matrices should go now.
  warn(


In [26]:
df = adata_p.obs[['seurat_clusters']]

In [27]:
df

seurat_clusters
L1_CACTTCGACAGCGTTAGCGAGTAA                30
L1_AGAGTCAAAGCCATGCGACTAGTA                30
L1_ACAAGCTATGGCTTCAAGATGTAC                30
L1_AACGCTTAGTCGTAGAAGATCGCA                30
L1_ATCCTGTAGAATCTGATCCGTCTA                30
...                                       ...
L25_ACGCTCGACGACACACCAAGGAGC                2
L25_AGAGTCAAGAGTTAGCCCGAAGTA               36
L25_ACGTATCAACACAGAAAGGCTAAC                2
L25_ACAGCAGAAGTGGTCAACCACTGT               36
L25_ACGTATCAGACAGTGCAGTACAAG               25

[103654 rows x 1 columns]

In [ ]:
# df.to_csv('clusters_per_cell.tsv', sep="\t")

# counts per replicate & cluster

In [28]:
mapping = pd.read_table("raw/LibraryNumberToTypeMapping.txt", header=None)
mapping.columns = ["prefix", "experiment", "group", "group_name"]
mapping["biological_replicate"] = ["ACME", "ACME", "ACME", "sample8", "sample8", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi", "sample7", "sample7", "sample13", "sample13", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi", "sample11_WT", "sample11_RNAi"]
mapping = mapping[["prefix", "group_name", "biological_replicate"]].set_index("prefix")
mapping

group_name biological_replicate
prefix                                
L1            WT1                 ACME
L2            WT1                 ACME
L3            WT1                 ACME
L4            WT2              sample8
L5            WT2              sample8
L6            WT4          sample11_WT
L7            NaN        sample11_RNAi
L8            WT4          sample11_WT
L9            NaN        sample11_RNAi
L10           WT3              sample7
L11           WT3              sample7
L12           NaN             sample13
L13           NaN             sample13
L14           WT4          sample11_WT
L15           NaN        sample11_RNAi
L16           WT4          sample11_WT
L17           NaN        sample11_RNAi
L18           WT4          sample11_WT
L19           NaN        sample11_RNAi
L20           WT4          sample11_WT
L21           NaN        sample11_RNAi
L22           WT4          sample11_WT
L23           NaN        sample11_RNAi
L24           WT4          sample11_WT
L25           NaN        sample11_RNAi

In [32]:
df2 = df.copy()
df2["biological_replicate"] = df2.index.map(lambda x: mapping.at[x.split("_")[0], "biological_replicate"])

df2[df2.index.str.contains("L11")].head()

seurat_clusters biological_replicate
L11_CACTTCGAAGATGTACAAGAGATC               25              sample7
L11_AGTGGTCACGGATTGCCAACCACA                0              sample7
L11_ATGCCTAATTCACGCAGTGTTCTA                9              sample7
L11_AGAGTCAAACATTGGCTGGAACAA               36              sample7
L11_CGCATACAAAGAGATCGTCTGTCA               14              sample7

In [37]:
cluster_counts = pd.DataFrame()

seurat_clusters = sorted(df2['seurat_clusters'].unique())
for cluster in seurat_clusters:

    cells_per_cluster_df = df2[df2['seurat_clusters'] == cluster]
    cluster_replicates = sorted(cells_per_cluster_df["biological_replicate"].unique())
    
    # sum the read counts per biological replicate, for this cluster
    for replicate in cluster_replicates:
        replicate_cells = cells_per_cluster_df[cells_per_cluster_df["biological_replicate"] == replicate].index
        
        replicate_df = counts[replicate_cells].sum(1).astype(int)
        replicate_df.name = f"{replicate}_cluster{cluster}"
        
        # add the "replicate" counts to the counts df
        cluster_counts = pd.concat([cluster_counts, replicate_df], axis=1)

cluster_counts

ACME_cluster0  sample11_RNAi_cluster0  sample11_WT_cluster0  \
SMEST000017001              2                       0                     2   
SMEST000022001              0                       0                     0   
SMEST000026001              1                       0                     0   
SMEST000041001              0                       0                     1   
SMEST000044001              1                       0                     0   
...                       ...                     ...                   ...   
SmMSTRG.16649               0                       0                     0   
SmMSTRG.20594               0                       0                     0   
SmMSTRG.3240                0                       0                     0   
SmMSTRG.6932                0                       0                     0   
SmMSTRG.7942                0                       0                     0   

                sample13_cluster0  sample7_cluster0  sample8_cluster0  \
SMEST000017001                  2                 2                 1   
SMEST000022001                  0                 0                 0   
SMEST000026001                  0                 0                 1   
SMEST000041001                  0                 0                 0   
SMEST000044001                  0                 0                 0   
...                           ...               ...               ...   
SmMSTRG.16649                   0                 0                 0   
SmMSTRG.20594                   0                 0                 0   
SmMSTRG.3240                    0                 0                 0   
SmMSTRG.6932                    0                 0                 0   
SmMSTRG.7942                    0                 0                 0   

                ACME_cluster1  sample11_RNAi_cluster1  sample11_WT_cluster1  \
SMEST000017001              0                       0                     0   
SMEST000022001              0                       0                     0   
SMEST000026001              0                       0                     0   
SMEST000041001              1                       0                     0   
SMEST000044001              5                       0                     0   
...                       ...                     ...                   ...   
SmMSTRG.16649               0                       0                     0   
SmMSTRG.20594               0                       0                     0   
SmMSTRG.3240                0                       0                     0   
SmMSTRG.6932                0                       0                     0   
SmMSTRG.7942                0                       0                     0   

                sample13_cluster1  ...  sample11_WT_cluster48  \
SMEST000017001                  0  ...                      0   
SMEST000022001                  0  ...                      0   
SMEST000026001                  0  ...                      0   
SMEST000041001                  0  ...                      0   
SMEST000044001                  0  ...                      0   
...                           ...  ...                    ...   
SmMSTRG.16649                   0  ...                      0   
SmMSTRG.20594                   0  ...                      0   
SmMSTRG.3240                    0  ...                      0   
SmMSTRG.6932                    0  ...                      0   
SmMSTRG.7942                    0  ...                      0   

                sample13_cluster48  sample7_cluster48  sample8_cluster48  \
SMEST000017001                   0                  0                  0   
SMEST000022001                   0                  0                  0   
SMEST000026001                   0                  0                  0   
SMEST000041001                   0                  0                  0   
SMEST000044001                   0                  0                  0   
... 

In [38]:
tpms = counts2tpm(cluster_counts.join(lengths))
tpms.head()

ACME_cluster0  sample11_RNAi_cluster0  sample11_WT_cluster0  \
SMEST000017001       2.238204                     0.0              4.145983   
SMEST000022001       0.000000                     0.0              0.000000   
SMEST000026001       0.202079                     0.0              0.000000   
SMEST000041001       0.000000                     0.0              0.650806   
SMEST000044001       0.492010                     0.0              0.000000   

                sample13_cluster0  sample7_cluster0  sample8_cluster0  \
SMEST000017001           6.968442          6.357948          2.338312   
SMEST000022001           0.000000          0.000000          0.000000   
SMEST000026001           0.000000          0.000000          0.422235   
SMEST000041001           0.000000          0.000000          0.000000   
SMEST000044001           0.000000          0.000000          0.000000   

                ACME_cluster1  sample11_RNAi_cluster1  sample11_WT_cluster1  \
SMEST000017001       0.000000                     0.0                   0.0   
SMEST000022001       0.000000                     0.0                   0.0   
SMEST000026001       0.000000                     0.0                   0.0   
SMEST000041001       0.104427                     0.0                   0.0   
SMEST000044001       0.731192                     0.0                   0.0   

                sample13_cluster1  ...  sample11_WT_cluster48  \
SMEST000017001                0.0  ...                    0.0   
SMEST000022001                0.0  ...                    0.0   
SMEST000026001                0.0  ...                    0.0   
SMEST000041001                0.0  ...                    0.0   
SMEST000044001                0.0  ...                    0.0   

                sample13_cluster48  sample7_cluster48  sample8_cluster48  \
SMEST000017001                 0.0                0.0                0.0   
SMEST000022001                 0.0                0.0                0.0   
SMEST000026001                 0.0                0.0                0.0   
SMEST000041001                 0.0                0.0                0.0   
SMEST000044001                 0.0                0.0                0.0   

                ACME_cluster49  sample11_RNAi_cluster49  \
SMEST000017001             0.0                      0.0   
SMEST000022001             0.0                      0.0   
SMEST000026001             0.0                      0.0   
SMEST000041001             0.0                      0.0   
SMEST000044001             0.0                      0.0   

                sample11_WT_cluster49  sample13_cluster49  sample7_cluster49  \
SMEST000017001                    0.0                 0.0                0.0   
SMEST000022001                    0.0                 0.0                0.0   
SMEST000026001                    0.0                 0.0                0.0   
SMEST000041001                    0.0                 0.0                0.0   
SMEST000044001                    0.0                 0.0                0.0   

                sample8_cluster49  
SMEST000017001                0.0  
SMEST000022001                0.0  
SMEST000026001                0.0  
SMEST000041001                0.0  
SMEST000044001                0.0  

[5 rows x 299 columns]

In [43]:
cluster_counts.to_csv('counts_per_replicate_cluster.tsv', sep="\t")
tpms.to_csv('tpms_per_replicate_cluster.tsv', sep="\t")

In [39]:
samples = pd.DataFrame({
    "sample": cluster_counts.columns, 
    "assembly": "Smed", 
    "experiment": [col.split("_cluster")[0] for col in cluster_counts.columns],
    "cluster": [col.split("_cluster")[1] for col in cluster_counts.columns],
}).set_index("sample")

samples.shape

(299, 3)

In [40]:
cells = []
for idx, (c,e) in samples[["cluster", "experiment"]].iterrows():
    tmp = df2[df2["seurat_clusters"] == int(c)]
    tmp = tmp[tmp["biological_replicate"] == e]
    
    cells.append(len(tmp))

len(cells)

299

In [41]:
samples["cells"] = cells
samples

assembly     experiment cluster  cells
sample                                                        
ACME_cluster0               Smed           ACME       0   3299
sample11_RNAi_cluster0      Smed  sample11_RNAi       0   1375
sample11_WT_cluster0        Smed    sample11_WT       0   1225
sample13_cluster0           Smed       sample13       0   1018
sample7_cluster0            Smed        sample7       0    887
...                          ...            ...     ...    ...
sample11_RNAi_cluster49     Smed  sample11_RNAi      49      7
sample11_WT_cluster49       Smed    sample11_WT      49      4
sample13_cluster49          Smed       sample13      49     33
sample7_cluster49           Smed        sample7      49      8
sample8_cluster49           Smed        sample8      49     81

[299 rows x 4 columns]

In [20]:
notes = pd.read_table('raw/Colour_matching_RNAseq.tsv')
notes.head(2)

cluster         notes
0        0  ChAT neurons
1        1   neoblasts 1

In [ ]:
samples = samples.merge(notes, left_on="cluster", right_on="cluster")
samples

In [19]:
samples.to_csv('samples_per_replicate_cluster.tsv', sep="\t")

# counts per (2) artificial replicates per cluster

In [ ]:
# cluster_counts = pd.DataFrame()

# # randomly shuffle the samples
# df = df.sample(frac=1, axis=0)

# for cluster in df['seurat_clusters'].unique():    
#     # split each cluster in two
#     subdf = df[df['seurat_clusters'] == cluster]
#     replicate_dfs = np.array_split(subdf, 2)
    
#     # sum the counts per "replicate"
#     for n, replicate_cells in enumerate(replicate_dfs):
#         replicate_cells = replicate_cells.index
        
#         replicate_df = counts[replicate_cells].sum(1).astype(int)
#         replicate_df.name = f"cluster{cluster}-{n}"
        
#         # add the "replicate" counts to the counts df
#         cluster_counts = pd.concat([cluster_counts, replicate_df], axis=1)

# cluster_counts


In [ ]:
# tpms = counts2tpm(cluster_counts.join(lengths))

In [ ]:
# cluster_counts.to_csv('counts_per_artificial_replicate.tsv', sep="\t")
# tpms.to_csv('tpms_per_artificial_replicate.tsv', sep="\t")

# split cluster in equal sized "replicates" (don't)

In [ ]:
# # the number of cells in the smallest cluster / 2 
# # (so that even this cluster has 2 replicates)
# # (and each replicate has equal samples)
# cells_per_replicate = math.ceil(df.groupby(['seurat_clusters']).size().min() / 2)

# print("cells_per_replicate", cells_per_replicate)

In [ ]:
# cluster_counts = pd.DataFrame()

# # randomly shuffle the samples
# df = df.sample(frac=1, axis=0)

# for cluster in df['seurat_clusters'].unique():    
#     # split the cells into subgroups of roughly equal size
#     subdf = df[df['seurat_clusters'] == cluster]
#     replicates = math.ceil(len(subdf) / cells_per_replicate)
#     replicate_dfs = np.array_split(subdf, replicates)
    
#     # sum the counts per "replicate"
#     for n, replicate_cells in enumerate(replicate_dfs):
#         replicate_cells = replicate_cells.index
        
#         replicate_df = counts[replicate_cells].sum(1).astype(int)
#         replicate_df.name = f"cluster{cluster}-{n}"
        
#         # add the "replicate" counts to the counts df
#         cluster_counts = pd.concat([cluster_counts, replicate_df], axis=1)

# cluster_counts


In [ ]:
# cluster_counts.to_csv('counts/counts_per_replicate.tsv', sep="\t")